In [5]:
# Gerekli kütüphaneleri yükleyelim
import pandas as pd
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import OneHotEncoder
import lightgbm as lgb
from catboost import CatBoostRegressor
import numpy as np

# Veri yolları
train_path = "C:/Users/ASUS/Desktop/Regression of Used Car Prices/train.csv"
test_path = "C:/Users/ASUS/Desktop/Regression of Used Car Prices/test.csv"

# Verileri yükleyin
train_data = pd.read_csv(train_path)
test_data = pd.read_csv(test_path)

# Eksik verileri doldurma
train_data['clean_title'].fillna('Unknown', inplace=True)
test_data['clean_title'].fillna('Unknown', inplace=True)

# Kategorik verileri one-hot encoding ile sayısal değerlere dönüştürme
categorical_columns = ['brand', 'model', 'fuel_type', 'engine', 'transmission', 'ext_col', 'int_col', 'accident', 'clean_title']
encoder = OneHotEncoder(handle_unknown='ignore', sparse_output=False)
encoded_train_array = encoder.fit_transform(train_data[categorical_columns])
encoded_test_array = encoder.transform(test_data[categorical_columns])

# Encoder tarafından oluşturulan yeni sütun adlarını alalım
encoded_columns = encoder.get_feature_names_out(categorical_columns)

# Numpy array'lerini DataFrame'e çevirirken sütun adlarını ekleyelim
encoded_train_data = pd.DataFrame(encoded_train_array, columns=encoded_columns, index=train_data.index)
encoded_test_data = pd.DataFrame(encoded_test_array, columns=encoded_columns, index=test_data.index)

# Orijinal veriyle birleştirme
train_data = train_data.join(encoded_train_data).drop(columns=categorical_columns)
test_data = test_data.join(encoded_test_data).drop(columns=categorical_columns)

# Bağımlı ve bağımsız değişkenler
X = train_data.drop(columns=['price', 'id'])
y = train_data['price']

# Veri setini eğitim ve doğrulama setlerine ayırma
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=42)

# LightGBM ve CatBoost modellerini tanımlama
lgb_model = lgb.LGBMRegressor()
catboost_model = CatBoostRegressor(allow_writing_files=False)

# Hiperparametre aralıklarını belirleme
param_dist_lgb = {
    'num_leaves': [31, 50, 100, 200, 255],
    'max_depth': [5, 10, 15],
    'learning_rate': [0.01, 0.05, 0.2],
    'n_estimators': [100, 500, 750],
    'min_child_samples': [10, 30],
    'subsample': [0.7, 0.9, 1.0],
    'colsample_bytree': [0.6, 0.8, 0.9]
}

param_dist_cat = {
    'depth': [6, 8, 10, 12],
    'learning_rate': [0.01, 0.05, 0.1],
    'iterations': [100, 500, 750],
    'l2_leaf_reg': [1, 3, 5],
    'border_count': [32, 50, 100]
}

# RandomizedSearchCV ile hiperparametre optimizasyonu
random_search_lgb = RandomizedSearchCV(
    estimator=lgb_model,
    param_distributions=param_dist_lgb,
    n_iter=50,
    scoring='neg_root_mean_squared_error',
    cv=3,
    verbose=3,
    random_state=42,
)

random_search_cat = RandomizedSearchCV(
    estimator=catboost_model,
    param_distributions=param_dist_cat,
    n_iter=50,
    scoring='neg_root_mean_squared_error',
    cv=3,
    verbose=3,
    random_state=42,
)

# Optimizasyonlu modelleri eğitme
random_search_lgb.fit(X_train, y_train)
random_search_cat.fit(X_train, y_train)

# En iyi hiperparametreleri al
best_lgb_model = random_search_lgb.best_estimator_
best_catboost_model = random_search_cat.best_estimator_

# Validation seti üzerindeki tahminleri yap
y_pred_lgb = best_lgb_model.predict(X_valid)
y_pred_catboost = best_catboost_model.predict(X_valid)

# Performans değerlendirmesi (RMSE)
rmse_lgb = mean_squared_error(y_valid, y_pred_lgb, squared=False)
rmse_catboost = mean_squared_error(y_valid, y_pred_catboost, squared=False)

print(f"Validation RMSE (LightGBM): {rmse_lgb}")
print(f"Validation RMSE (CatBoost): {rmse_catboost}")
print(f"En iyi hiperparametreler (LightGBM): {random_search_lgb.best_params_}")
print(f"En iyi hiperparametreler (CatBoost): {random_search_cat.best_params_}")

# Ensemble tahminleri (ortalama)
y_pred_ensemble = (y_pred_lgb + y_pred_catboost) / 2

# Ensemble performans değerlendirmesi (RMSE)
rmse_ensemble = mean_squared_error(y_valid, y_pred_ensemble, squared=False)
print(f"Validation RMSE (Ensemble): {rmse_ensemble}")


Fitting 3 folds for each of 50 candidates, totalling 150 fits
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.055754 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3486
[LightGBM] [Info] Number of data points in the train set: 100550, number of used features: 1600
[LightGBM] [Info] Start training from score 43937.817315
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

497:	learn: 68737.2423683	total: 5.56s	remaining: 22.3ms
498:	learn: 68727.2715420	total: 5.57s	remaining: 11.2ms
499:	learn: 68717.4678196	total: 5.58s	remaining: 0us
[CV 3/3] END border_count=32, depth=6, iterations=500, l2_leaf_reg=5, learning_rate=0.05;, score=-75308.519 total time=   7.8s
0:	learn: 79745.5545057	total: 209ms	remaining: 1m 44s
1:	learn: 79651.5979623	total: 424ms	remaining: 1m 45s
2:	learn: 79557.6536973	total: 634ms	remaining: 1m 45s
3:	learn: 79466.4011327	total: 817ms	remaining: 1m 41s
4:	learn: 79376.5395787	total: 998ms	remaining: 1m 38s
5:	learn: 79285.3879406	total: 1.18s	remaining: 1m 36s
6:	learn: 79196.2387357	total: 1.36s	remaining: 1m 35s
7:	learn: 79110.1479581	total: 1.54s	remaining: 1m 34s
8:	learn: 79020.4932313	total: 1.77s	remaining: 1m 36s
9:	learn: 78941.9873069	total: 1.96s	remaining: 1m 35s
10:	learn: 78859.8647105	total: 2.14s	remaining: 1m 35s
11:	learn: 78778.3445244	total: 2.24s	remaining: 1m 31s
12:	learn: 78698.4522557	total: 2.42s	remai

142:	learn: 73954.9550486	total: 27.5s	remaining: 1m 8s
143:	learn: 73937.4238750	total: 27.7s	remaining: 1m 8s
144:	learn: 73920.7730153	total: 27.9s	remaining: 1m 8s
145:	learn: 73905.5200838	total: 28.1s	remaining: 1m 8s
146:	learn: 73890.9252931	total: 28.2s	remaining: 1m 7s
147:	learn: 73872.5172834	total: 28.4s	remaining: 1m 7s
148:	learn: 73857.3513731	total: 28.7s	remaining: 1m 7s
149:	learn: 73842.7056564	total: 28.9s	remaining: 1m 7s
150:	learn: 73827.6427882	total: 29.1s	remaining: 1m 7s
151:	learn: 73809.4783195	total: 29.2s	remaining: 1m 6s
152:	learn: 73792.7702637	total: 29.4s	remaining: 1m 6s
153:	learn: 73776.0944023	total: 29.7s	remaining: 1m 6s
154:	learn: 73761.6042480	total: 29.9s	remaining: 1m 6s
155:	learn: 73747.4688859	total: 30s	remaining: 1m 6s
156:	learn: 73731.5785590	total: 30.2s	remaining: 1m 6s
157:	learn: 73717.5266655	total: 30.4s	remaining: 1m 5s
158:	learn: 73704.8084125	total: 30.6s	remaining: 1m 5s
159:	learn: 73691.5386115	total: 30.8s	remaining: 

290:	learn: 72333.6413938	total: 57s	remaining: 41s
291:	learn: 72327.3980375	total: 57.2s	remaining: 40.8s
292:	learn: 72319.7080876	total: 57.4s	remaining: 40.6s
293:	learn: 72312.4767586	total: 57.7s	remaining: 40.4s
294:	learn: 72304.6732078	total: 57.9s	remaining: 40.2s
295:	learn: 72297.3468308	total: 58.1s	remaining: 40s
296:	learn: 72290.2223398	total: 58.3s	remaining: 39.8s
297:	learn: 72281.1839530	total: 58.5s	remaining: 39.6s
298:	learn: 72271.8291028	total: 58.7s	remaining: 39.5s
299:	learn: 72263.3884102	total: 58.9s	remaining: 39.3s
300:	learn: 72254.3849791	total: 59.1s	remaining: 39.1s
301:	learn: 72247.6921021	total: 59.3s	remaining: 38.9s
302:	learn: 72244.7763610	total: 59.5s	remaining: 38.7s
303:	learn: 72241.1711028	total: 59.7s	remaining: 38.5s
304:	learn: 72232.7978965	total: 59.9s	remaining: 38.3s
305:	learn: 72226.2886999	total: 1m	remaining: 38.1s
306:	learn: 72218.6663649	total: 1m	remaining: 37.9s
307:	learn: 72210.4102464	total: 1m	remaining: 37.7s
308:	le

436:	learn: 71467.8756829	total: 1m 30s	remaining: 13s
437:	learn: 71461.3081477	total: 1m 30s	remaining: 12.9s
438:	learn: 71454.1892918	total: 1m 31s	remaining: 12.7s
439:	learn: 71447.5649674	total: 1m 31s	remaining: 12.5s
440:	learn: 71443.0239988	total: 1m 31s	remaining: 12.3s
441:	learn: 71437.1988626	total: 1m 31s	remaining: 12.1s
442:	learn: 71432.3478526	total: 1m 32s	remaining: 11.9s
443:	learn: 71424.5727742	total: 1m 32s	remaining: 11.7s
444:	learn: 71420.3912538	total: 1m 32s	remaining: 11.5s
445:	learn: 71412.8707137	total: 1m 32s	remaining: 11.2s
446:	learn: 71406.5696776	total: 1m 33s	remaining: 11s
447:	learn: 71400.9525390	total: 1m 33s	remaining: 10.8s
448:	learn: 71393.9422779	total: 1m 33s	remaining: 10.6s
449:	learn: 71387.4648785	total: 1m 33s	remaining: 10.4s
450:	learn: 71381.3516916	total: 1m 33s	remaining: 10.2s
451:	learn: 71377.1946549	total: 1m 34s	remaining: 10s
452:	learn: 71370.6911652	total: 1m 34s	remaining: 9.8s
453:	learn: 71364.9505943	total: 1m 34

C:\Users\ASUS\anaconda3\Lib\site-packages\sklearn\metrics\_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
C:\Users\ASUS\anaconda3\Lib\site-packages\sklearn\metrics\_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
C:\Users\ASUS\anaconda3\Lib\site-packages\sklearn\metrics\_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(


In [7]:
# 6. Batch'ler Halinde Test Setinde Tahminler
batch_size = 1000
all_predictions = pd.DataFrame()

for i in range(0, len(test_data), batch_size):
    batch = test_data[i:i+batch_size]
    batch_predictions = best_lgb_model.predict(batch.drop(columns=['id']))
    
    batch_output = pd.DataFrame({'id': batch['id'], 'price': batch_predictions})
    all_predictions = pd.concat([all_predictions, batch_output])

# 7. Sonuçları CSV Dosyasına Kaydetme
all_predictions.to_csv('predictions.csv', index=False)